## Importing Data

In [1]:
import pandas as pd
import sys
import codecs
import nltk
from nltk.corpus import stopwords
from nltk import ngrams

import matplotlib
import matplotlib.pyplot as plt

pd.set_option('display.max_colwidth', -1)
pd.set_option('display.max_rows', 500)

In [2]:
# getting data

one_ic = pd.read_csv('../data/1-ic.csv')
one_gc = pd.read_csv('../data/1-gc.csv')
one_sc = pd.read_csv('../data/1-sc.csv')

two_jm = pd.read_csv('../data/2-jm.csv')
two_mg = pd.read_csv('../data/2-mg.csv')
two_nb = pd.read_csv('../data/2-nb.csv')

three_rs = pd.read_csv('../data/3-rs.csv')
three_rt = pd.read_csv('../data/3-rt.csv')
three_sj = pd.read_csv('../data/3-sj.csv')

In [3]:
tph_batch1 = pd.read_csv('../data/tph_batch1.csv')

In [4]:
tph_batch1.head()

sampled_bid_id               message_timestamp message_sender  \
0  18314236        2018-01-31 23:16:50.788616 UTC  Customer        
1  27365009        2018-02-11 16:54:15.485935 UTC  Customer        
2  27365009        2018-02-11 22:20:38.481901 UTC  Pro             
3  27365009        2018-02-13 20:02:41.064269 UTC  Customer        
4  27365009        2018-02-13 22:28:17.518399 UTC  Pro             

                                                                                                                                                                                                                                                                                                                                                                                                                                                            message  \
0  Hello Brian. You helped us a few years back and we are in need of an electrician again!  Are you able to install a new electrical hook up for a new spa we have purchased?  It requires a dedicated hook up for a 240v spa and will be outdoors. We are in Bay Park area just off I-5. Please let me know... Thanks!                                                                                                                                               
1  Sounds good! What's next?                                                                                                                                                                                                                                                                                                                                                                                                                                          
2  Hi Cayatana, nice to &quotesee&quote you back! Since it's been two years since we last spoke, perhaps you can tell me if you are still looking for the same thing. How would you like to work together...remotely or in-person? What is your schedule like? Once we determine our first session, you would send payment before hand to my PayPal account before we proceed. I will also send you some forms to complete prior to our session, as well. Best, Amy   
3  Hi! I’m currently traveling but will reach out as soon as I get back. Thanks!                                                                                                                                                                                                                                                                                                                                                                                      
4  Sounds good and safe travels! Best, Amy                                                                                                                                                                                                                                                                                                                                                                                                                            

                       category agent_group  
0  Electrical and Wiring Repair  agent_3     
1  Nutritionist                  agent_2     
2  Nutritionist                  agent_2     
3  Nutritionist                  agent_2     
4  Nutritionist                  agent_2

### One

In [5]:
one_gc_labels = one_gc[['Label 1', 'Label 2', 'Label 3', 'Label 4', 'Label 5']]
one_sc_labels = one_sc[['Label 1', 'Label 2', 'Label 3', 'Label 4', 'Label 5']]
one = one_ic.merge(one_gc_labels, left_index=True, right_index=True)
one = one.merge(one_sc_labels, left_index=True, right_index=True)

### Two

In [6]:
two_mg_labels = two_mg[['Label 1', 'Label 2', 'Label 3', 'Label 4', 'Label 5']]
two_nb_labels = two_nb[['Label 1', 'Label 2', 'Label 3', 'Label 4', 'Label 5']]
two = two_jm.merge(two_mg_labels, left_index=True, right_index=True)
two = two.merge(two_nb_labels, left_index=True, right_index=True)

### Three

In [7]:
three_rt_labels = three_rt[['Label 1', 'Label 2', 'Label 3', 'Label 4', 'Label 5']]
three_sj_labels = three_sj[['Label 1', 'Label 2', 'Label 3', 'Label 4', 'Label 5']]
three = three_rs.merge(three_rt_labels, left_index=True, right_index=True)
three = three.merge(three_sj_labels, left_index=True, right_index=True)

### Concatenate DFs

In [8]:
# all three dataframes have the same shape
print(three.shape)
print(one.shape)
print(two.shape)

(4999, 22)
(5040, 22)
(5003, 22)


In [9]:
# df is batch 1 data, but conversation level
labels = pd.concat([one, two, three], ignore_index=True)

In [10]:
labels['Label 1_x'].unique()

array(['Scheduling - Meeting or Job', 'Price', 'Location', 'Job Details',
       'Generic Answer', 'Contact Information', 'Confirmation - Meeting',
       nan, 'Follow-up', 'Confirmation - Contact', 'Considering', 'Hire',
       'Rejection', 'Payment'], dtype=object)

In [11]:
#tph_batch1.columns = ['bid_id']
tph_batch1.rename({'sampled_bid_id': 'bid_id'}, axis='columns', inplace=True)

### Hire

In [12]:
def is_hire(value):
    if value == "Hire":
        return 1
    else:
        return 0

In [13]:
hire = labels.applymap(is_hire)
hires = hire[["Label 1_x","Label 2_x", "Label 3_x", "Label 4_x", "Label 5_x",
              "Label 1_y","Label 2_y", "Label 3_y", "Label 4_y", "Label 5_y",
              'Label 1', 'Label 2', 'Label 3', 'Label 4', 'Label 5']].any(axis=1)
hires = hires[hires == True]
labels['is_hired'] = hires
labels['is_hired'].fillna(False, inplace=True)
hired = labels.loc[hires.index]

In [14]:
labels['is_hired'].shape

(15042,)

### Location

- location, contact information, scheduling - meeting or job, price, payment

In [15]:
def is_location(value):
    if value == "Location":
        return 1
    else:
        return 0

In [16]:
location = labels.applymap(is_location)
locations = location[["Label 1_x","Label 2_x", "Label 3_x", "Label 4_x", "Label 5_x",
              "Label 1_y","Label 2_y", "Label 3_y", "Label 4_y", "Label 5_y",
              'Label 1', 'Label 2', 'Label 3', 'Label 4', 'Label 5']].any(axis=1)
locations = locations[locations == True]
labels['is_location'] = locations
labels['is_location'].fillna(False, inplace=True)
is_location = labels.loc[locations.index]

In [10]:
labels['Label 1_x'].unique()

array(['Scheduling - Meeting or Job', 'Price', 'Location', 'Job Details',
       'Generic Answer', 'Contact Information', 'Confirmation - Meeting',
       nan, 'Follow-up', 'Confirmation - Contact', 'Considering', 'Hire',
       'Rejection', 'Payment'], dtype=object)

### Contact Information

- location, contact information, scheduling - meeting or job, price, payment

In [20]:
def is_contact_info(value):
    if value == "Contact Information":
        return 1
    else:
        return 0

In [21]:
contact_info = labels.applymap(is_contact_info)
contact_infos = contact_info[["Label 1_x","Label 2_x", "Label 3_x", "Label 4_x", "Label 5_x",
              "Label 1_y","Label 2_y", "Label 3_y", "Label 4_y", "Label 5_y",
              'Label 1', 'Label 2', 'Label 3', 'Label 4', 'Label 5']].any(axis=1)
contact_infos = contact_infos[contact_infos == True]
labels['is_contact_info'] = contact_infos
labels['is_contact_info'].fillna(False, inplace=True)
is_contact_info = labels.loc[contact_infos.index]

### Scheduling

- price, payment

In [23]:
def is_scheduling(value):
    if value == "Scheduling - Meeting or Job":
        return 1
    else:
        return 0

In [24]:
scheduling = labels.applymap(is_scheduling)
schedulings = scheduling[["Label 1_x","Label 2_x", "Label 3_x", "Label 4_x", "Label 5_x",
              "Label 1_y","Label 2_y", "Label 3_y", "Label 4_y", "Label 5_y",
              'Label 1', 'Label 2', 'Label 3', 'Label 4', 'Label 5']].any(axis=1)
schedulings = schedulings[schedulings == True]
labels['is_scheduling'] = schedulings
labels['is_scheduling'].fillna(False, inplace=True)
is_scheduling = labels.loc[schedulings.index]

### Price

In [37]:
def is_price(value):
    if value == "Price":
        return 1
    else:
        return 0

In [38]:
price = labels.applymap(is_price)
prices = price[["Label 1_x","Label 2_x", "Label 3_x", "Label 4_x", "Label 5_x",
              "Label 1_y","Label 2_y", "Label 3_y", "Label 4_y", "Label 5_y",
              'Label 1', 'Label 2', 'Label 3', 'Label 4', 'Label 5']].any(axis=1)
prices = prices[prices == True]
labels['is_price'] = prices
labels['is_price'].fillna(False, inplace=True)
is_price = labels.loc[prices.index]

### Payment

In [39]:
def is_payment(value):
    if value == "Payment":
        return 1
    else:
        return 0

In [40]:
payment = labels.applymap(is_payment)
payments = payment[["Label 1_x","Label 2_x", "Label 3_x", "Label 4_x", "Label 5_x",
              "Label 1_y","Label 2_y", "Label 3_y", "Label 4_y", "Label 5_y",
              'Label 1', 'Label 2', 'Label 3', 'Label 4', 'Label 5']].any(axis=1)
payments = payments[payments == True]
labels['is_payment'] = payments
labels['is_payment'].fillna(False, inplace=True)
is_payment = labels.loc[payments.index]

In [41]:
labels.head()

bid_id  bid_id_header               message_timestamp message_sender  \
0  29404730  29404730.0     2017-11-04 01:24:06.036065 UTC  Customer        
1  30265067  30265067.0     2018-04-03 17:58:48.35945 UTC   Customer        
2  30265067 NaN             2018-04-03 17:59:45.382072 UTC  Customer        
3  30265067 NaN             2018-04-03 18:29:00.359911 UTC  Pro             
4  30265067 NaN             2018-04-03 18:56:44.639868 UTC  Customer        

                                                                                                      pii_cleaned_message  \
0  Greetings..\nAre you available for resume writing?                                                                       
1  What's your next availability?                                                                                           
2  I would like to get an  estimate for siding repair                                                                       
3  April. Can likely do est this wk & Work maybe the next. let me know your phone # & address.  [LOCATION]. [PERSON_NAME]   
4  [LOCATION] [PHONE_NUMBER]                                                                                                

                     Label 1_x            Label 2_x Label 3_x Label 4_x  \
0  Scheduling - Meeting or Job  NaN                  NaN       NaN        
1  Scheduling - Meeting or Job  NaN                  NaN       NaN        
2  Price                        Job Details          NaN       NaN        
3  Scheduling - Meeting or Job  Contact Information  Location  Price      
4  Location                     Contact Information  NaN       NaN        

  Label 5_x    ...                  Label 2   Label 3 Label 4 Label 5  \
0  NaN         ...      NaN                  NaN       NaN     NaN      
1  NaN         ...      NaN                  NaN       NaN     NaN      
2  NaN         ...      Job Details          NaN       NaN     NaN      
3  NaN         ...      Contact Information  Location  Price   NaN      
4  NaN         ...      Contact Information  NaN       NaN     NaN      

  is_hired is_location is_contact_info is_scheduling is_price is_payment  
0  False    False       False           True          False    False      
1  False    False       False           True          False    False      
2  False    False       False           False         True     False      
3  False    True        True            True          True     False      
4  False    True        True            False         False    False      

[5 rows x 28 columns]

### Locations

In [42]:
is_location[is_location.message_sender == 'Customer'][['message_sender', 'pii_cleaned_message', 'category']].shape

(1092, 3)

In [43]:
is_location.shape

(2206, 24)

In [50]:
tph_batch1.head()

bid_id               message_timestamp message_sender  \
0  18314236  2018-01-31 23:16:50.788616 UTC  Customer        
1  27365009  2018-02-11 16:54:15.485935 UTC  Customer        
2  27365009  2018-02-11 22:20:38.481901 UTC  Pro             
3  27365009  2018-02-13 20:02:41.064269 UTC  Customer        
4  27365009  2018-02-13 22:28:17.518399 UTC  Pro             

                                                                                                                                                                                                                                                                                                                                                                                                                                                            message  \
0  Hello Brian. You helped us a few years back and we are in need of an electrician again!  Are you able to install a new electrical hook up for a new spa we have purchased?  It requires a dedicated hook up for a 240v spa and will be outdoors. We are in Bay Park area just off I-5. Please let me know... Thanks!                                                                                                                                               
1  Sounds good! What's next?                                                                                                                                                                                                                                                                                                                                                                                                                                          
2  Hi Cayatana, nice to &quotesee&quote you back! Since it's been two years since we last spoke, perhaps you can tell me if you are still looking for the same thing. How would you like to work together...remotely or in-person? What is your schedule like? Once we determine our first session, you would send payment before hand to my PayPal account before we proceed. I will also send you some forms to complete prior to our session, as well. Best, Amy   
3  Hi! I’m currently traveling but will reach out as soon as I get back. Thanks!                                                                                                                                                                                                                                                                                                                                                                                      
4  Sounds good and safe travels! Best, Amy                                                                                                                                                                                                                                                                                                                                                                                                                            

                       category agent_group  
0  Electrical and Wiring Repair  agent_3     
1  Nutritionist                  agent_2     
2  Nutritionist                  agent_2     
3  Nutritionist                  agent_2     
4  Nutritionist                  agent_2

In [53]:
tph_batch1.shape

(61048, 6)

In [54]:
pd.merge(tph_batch1, labels[['bid_id', 'message_timestamp', 'is_hired']], how='inner', on=["bid_id", "message_timestamp"]).shape

(15042, 7)

In [62]:
df = pd.merge(tph_batch1, labels[['bid_id', 'message_timestamp', 'is_hired']], on=["bid_id", "message_timestamp"])
df = pd.merge(df, labels[['bid_id', 'message_timestamp', 'is_location']], on=["bid_id", "message_timestamp"])
df = pd.merge(df, labels[['bid_id', 'message_timestamp', 'is_contact_info']], on=["bid_id", "message_timestamp"])
df = pd.merge(df, labels[['bid_id', 'message_timestamp', 'is_scheduling']], on=["bid_id", "message_timestamp"])
df = pd.merge(df, labels[['bid_id', 'message_timestamp', 'is_price']], on=["bid_id", "message_timestamp"])
df = pd.merge(df, labels[['bid_id', 'message_timestamp', 'is_payment']], on=["bid_id", "message_timestamp"])

In [64]:
df.head()

bid_id               message_timestamp message_sender  \
0  18314236  2018-01-31 23:16:50.788616 UTC  Customer        
1  27365009  2018-02-11 16:54:15.485935 UTC  Customer        
2  27365009  2018-02-11 22:20:38.481901 UTC  Pro             
3  27365009  2018-02-13 20:02:41.064269 UTC  Customer        
4  27365009  2018-02-13 22:28:17.518399 UTC  Pro             

                                                                                                                                                                                                                                                                                                                                                                                                                                                            message  \
0  Hello Brian. You helped us a few years back and we are in need of an electrician again!  Are you able to install a new electrical hook up for a new spa we have purchased?  It requires a dedicated hook up for a 240v spa and will be outdoors. We are in Bay Park area just off I-5. Please let me know... Thanks!                                                                                                                                               
1  Sounds good! What's next?                                                                                                                                                                                                                                                                                                                                                                                                                                          
2  Hi Cayatana, nice to &quotesee&quote you back! Since it's been two years since we last spoke, perhaps you can tell me if you are still looking for the same thing. How would you like to work together...remotely or in-person? What is your schedule like? Once we determine our first session, you would send payment before hand to my PayPal account before we proceed. I will also send you some forms to complete prior to our session, as well. Best, Amy   
3  Hi! I’m currently traveling but will reach out as soon as I get back. Thanks!                                                                                                                                                                                                                                                                                                                                                                                      
4  Sounds good and safe travels! Best, Amy                                                                                                                                                                                                                                                                                                                                                                                                                            

                       category agent_group  is_hired  is_location  \
0  Electrical and Wiring Repair  agent_3     False     True          
1  Nutritionist                  agent_2     False     False         
2  Nutritionist                  agent_2     False     False         
3  Nutritionist                  agent_2     False     False         
4  Nutritionist                  agent_2     False     False         

   is_contact_info  is_scheduling  is_price  is_payment  
0  False            False          False     False       
1  False            False          False     False       
2  False            True           False     True        
3  False            True           False     False       
4  False            False          False     False

### Location NLTK Freqdist

In [65]:
default_stopwords = set(nltk.corpus.stopwords.words('english'))

In [68]:
df.head()

bid_id               message_timestamp message_sender  \
0  18314236  2018-01-31 23:16:50.788616 UTC  Customer        
1  27365009  2018-02-11 16:54:15.485935 UTC  Customer        
2  27365009  2018-02-11 22:20:38.481901 UTC  Pro             
3  27365009  2018-02-13 20:02:41.064269 UTC  Customer        
4  27365009  2018-02-13 22:28:17.518399 UTC  Pro             

                                                                                                                                                                                                                                                                                                                                                                                                                                                            message  \
0  Hello Brian. You helped us a few years back and we are in need of an electrician again!  Are you able to install a new electrical hook up for a new spa we have purchased?  It requires a dedicated hook up for a 240v spa and will be outdoors. We are in Bay Park area just off I-5. Please let me know... Thanks!                                                                                                                                               
1  Sounds good! What's next?                                                                                                                                                                                                                                                                                                                                                                                                                                          
2  Hi Cayatana, nice to &quotesee&quote you back! Since it's been two years since we last spoke, perhaps you can tell me if you are still looking for the same thing. How would you like to work together...remotely or in-person? What is your schedule like? Once we determine our first session, you would send payment before hand to my PayPal account before we proceed. I will also send you some forms to complete prior to our session, as well. Best, Amy   
3  Hi! I’m currently traveling but will reach out as soon as I get back. Thanks!                                                                                                                                                                                                                                                                                                                                                                                      
4  Sounds good and safe travels! Best, Amy                                                                                                                                                                                                                                                                                                                                                                                                                            

                       category agent_group  is_hired  is_location  \
0  Electrical and Wiring Repair  agent_3     False     True          
1  Nutritionist                  agent_2     False     False         
2  Nutritionist                  agent_2     False     False         
3  Nutritionist                  agent_2     False     False         
4  Nutritionist                  agent_2     False     False         

   is_contact_info  is_scheduling  is_price  is_payment  
0  False            False          False     False       
1  False            False          False     False       
2  False            True           False     True        
3  False            True           False     False       
4  False            False          False     False

In [70]:
df[df.is_hired == True].shape

(602, 12)

In [71]:
df[df.is_location == True].shape

(2206, 12)

In [72]:
df[df.is_contact_info == True].shape

(2148, 12)

In [73]:
df[df.is_scheduling == True].shape

(6369, 12)

In [74]:
df[df.is_price == True].shape

(2962, 12)

In [75]:
df[df.is_payment == True].shape

(522, 12)

### Hiring

In [76]:
# https://stackoverflow.com/questions/17531684/n-grams-in-python-four-five-six-grams
# https://stackoverflow.com/questions/14364762/counting-n-gram-frequency-in-python-nltk
# https://www.strehle.de/tim/weblog/archives/2015/09/03/1569
# https://stackoverflow.com/questions/40206249/count-of-most-popular-words-in-a-pandas-dataframe

txt = df[df.is_hired == True].message.str.lower().str.replace(r'\|', ' ').str.cat(sep=' ')
words = nltk.tokenize.word_tokenize(txt)
#Create your bigrams
bigrams = nltk.bigrams(words)
trigrams = nltk.trigrams(words)
# fourgrams = ngrams(words.split(), 4)
fourgrams = ngrams(words,4)
fivegrams = ngrams(words,5)
word_dist = nltk.FreqDist(words)

top_N = 100

default_stopwords = set(nltk.corpus.stopwords.words('english'))
custom_stopwords = set((u'.', u',', u'?', u'!', u'would', u')', u':', u'\'s', u'('))
all_stopwords = default_stopwords | custom_stopwords

words_except_stop_dist = nltk.FreqDist(w for w in words if w not in all_stopwords) 

# print('All frequencies, including STOPWORDS:')
# print('=' * 60)
# rslt = pd.DataFrame(word_dist.most_common(top_N),
#                     columns=['Word', 'Frequency'])
# print(rslt)
# print('=' * 60)

print('Unigram frequencies, excluding STOPWORDS:')
rslt = pd.DataFrame(words_except_stop_dist.most_common(top_N),
                    columns=['Word', 'Frequency']).set_index('Word')

print(rslt)
print('=' * 60)

# Bigram Frequencies
print('Bigram frequencies:')
bigrams_freq = nltk.FreqDist(bigrams)
rslt = pd.DataFrame(bigrams_freq.most_common(top_N),
                    columns=['Word', 'Frequency']).set_index('Word')

print(rslt)
print('=' * 60)

# Trigram Frequencies
print('Trigram frequencies:')
trigrams_freq = nltk.FreqDist(trigrams)
rslt = pd.DataFrame(trigrams_freq.most_common(top_N),
                    columns=['Word', 'Frequency']).set_index('Word')

print(rslt)
print('=' * 60)

# Fourgram Frequencies
print('Fourgram frequencies:')
fourgrams_freq = nltk.FreqDist(fourgrams)
rslt = pd.DataFrame(fourgrams_freq.most_common(top_N),
                    columns=['Word', 'Frequency']).set_index('Word')

print(rslt)
print('=' * 60)

# matplotlib.style.use('ggplot')
# rslt.plot.bar(rot=0)

Unigram frequencies, excluding STOPWORDS:
                  Frequency
Word                       
hi                162      
review            156      
thank             136      
thanks            128      
get               101      
work              90       
thumbtack         90       
please            88       
see               83       
&                 72       
taking            70       
help              67       
appreciate        64       
know              60       
good              58       
great             58       
really            57       
let               57       
new               56       
write             55       
'd                54       
much              53       
time              52       
minutes           52       
need              51       
reviews           51       
advance           51       
send              50       
include           47       
profile           47       
n't               47       
important         46       
'll   

## Other

In [238]:
# https://stackoverflow.com/questions/17531684/n-grams-in-python-four-five-six-grams
# https://stackoverflow.com/questions/14364762/counting-n-gram-frequency-in-python-nltk
# https://www.strehle.de/tim/weblog/archives/2015/09/03/1569
# https://stackoverflow.com/questions/40206249/count-of-most-popular-words-in-a-pandas-dataframe

txt = df[df.is_payment == True].message.str.lower().str.replace(r'\|', ' ').str.cat(sep=' ')
words = nltk.tokenize.word_tokenize(txt)
#Create your bigrams
bigrams = nltk.bigrams(words)
trigrams = nltk.trigrams(words)
# fourgrams = ngrams(words.split(), 4)
fourgrams = ngrams(words,4)
fivegrams = ngrams(words,5)
word_dist = nltk.FreqDist(words)

top_N = 100

default_stopwords = set(nltk.corpus.stopwords.words('english'))
custom_stopwords = set((u'.', u',', u'?', u'!', u'would', u')', u':', u'\'s', u'('))
all_stopwords = default_stopwords | custom_stopwords

words_except_stop_dist = nltk.FreqDist(w for w in words if w not in all_stopwords) 

# print('All frequencies, including STOPWORDS:')
# print('=' * 60)
# rslt = pd.DataFrame(word_dist.most_common(top_N),
#                     columns=['Word', 'Frequency'])
# print(rslt)
# print('=' * 60)

print('Unigram frequencies, excluding STOPWORDS:')
rslt = pd.DataFrame(words_except_stop_dist.most_common(top_N),
                    columns=['Word', 'Frequency']).set_index('Word')

print(rslt)
print('=' * 60)

# Bigram Frequencies
print('Bigram frequencies:')
bigrams_freq = nltk.FreqDist(bigrams)
rslt = pd.DataFrame(bigrams_freq.most_common(top_N),
                    columns=['Word', 'Frequency']).set_index('Word')

print(rslt)
print('=' * 60)

# Trigram Frequencies
print('Trigram frequencies:')
trigrams_freq = nltk.FreqDist(trigrams)
rslt = pd.DataFrame(trigrams_freq.most_common(top_N),
                    columns=['Word', 'Frequency']).set_index('Word')

print(rslt)
print('=' * 60)

# Fourgram Frequencies
print('Fourgram frequencies:')
fourgrams_freq = nltk.FreqDist(fourgrams)
rslt = pd.DataFrame(fourgrams_freq.most_common(top_N),
                    columns=['Word', 'Frequency']).set_index('Word')

print(rslt)
print('=' * 60)

# matplotlib.style.use('ggplot')
# rslt.plot.bar(rot=0)

Unigram frequencies, excluding STOPWORDS:
           Frequency
Word                
$          131      
send       127      
payment    126      
check      123      
deposit    118      
get        102      
pay        100      
cash       99       
need       99       
like       91       
-          89       
know       88       
n't        86       
please     85       
work       84       
thanks     82       
email      82       
&          81       
also       81       
time       77       
thank      76       
let        73       
hi         63       
address    62       
take       61       
'll        59       
day        59       
credit     58       
contract   57       
yes        52       
'm         49       
make       49       
much       47       
invoice    47       
back       46       
one        44       
quote      43       
phone      43       
want       42       
could      42       
card       41       
great      41       
see        40       
date       40

### Customer Messages

- 1092 / 2206 are from customers
- 1114 / 2206 are from pros

## Regex Testing

In [83]:
df.columns

Index(['bid_id', 'message_timestamp', 'message_sender', 'message', 'category',
       'agent_group', 'is_hired', 'is_location', 'is_contact_info',
       'is_scheduling', 'is_price', 'is_payment'],
      dtype='object')

In [85]:
df[df.is_hired == True][['bid_id', 'message_sender', 'message', 'is_hired']]

bid_id message_sender  \
25     37749231  Pro             
133    48887274  Pro             
134    48887274  Customer        
135    48887274  Pro             
165    53924583  Customer        
212    54853421  Pro             
213    54853421  Pro             
214    54853421  Pro             
255    55577457  Customer        
321    56897154  Pro             
335    57273156  Customer        
337    57273156  Customer        
341    57273156  Pro             
356    57435440  Customer        
373    57435440  Customer        
374    57435440  Customer        
375    57435440  Pro             
391    57503841  Customer        
392    57503841  Pro             
393    57503841  Customer        
425    57602633  Customer        
474    57648519  Pro             
533    57715984  Customer        
539    57715984  Pro             
540    57715984  Pro             
566    57723640  Pro             
575    57723640  Customer        
579    57723640  Pro             
581    57723640  Pro             
586    57723640  Customer        
616    57725153  Pro             
617    57725153  Pro             
619    57725153  Customer        
620    57725153  Pro             
631    57729758  Pro             
645    57735946  Pro             
646    57735946  Pro             
647    57735946  Pro             
668    57744433  Pro             
677    57744433  Customer        
695    57745699  Customer        
721    57752819  Customer        
767    57767481  Pro             
820    57785390  Pro             
844    57788486  Customer        
845    57788486  Pro             
849    57788486  Customer        
878    57806273  Pro             
892    57820909  Pro             
968    57839525  Pro             
969    57839525  Customer        
971    57839525  Pro             
972    57839525  Customer        
1076   57882657  Customer        
1077   57882657  Pro             
1078   57882657  Customer        
1080   57882657  Pro             
1081   57882657  Customer        
1110   57901169  Customer        
1115   57901169  Pro             
1169   57952220  Customer        
1176   57954079  Customer        
1187   57956586  Customer        
1224   57973645  Customer        
1275   58001466  Customer        
1276   58001466  Pro             
1287   58020525  Pro             
1593   58087234  Pro             
1613   58099307  Pro             
1643   58105395  Pro             
1655   58118698  Pro             
1661   58119437  Customer        
1665   58119437  Pro             
1689   58129163  Customer        
1690   58129163  Pro             
1746   58144197  Customer        
1760   58144197  Customer        
1773   58144197  Pro             
1774   58144197  Pro             
1776   58144197  Customer        
1778   58144197  Pro             
1779   58144197  Customer        
1856   58172657  Customer        
1896   58175451  Customer        
1897   58175451  Pro             
1947   58200799  Customer        
1948   58200799  Pro             
1962   58201091  Pro             
1963   58201091  Customer        
2071   58258534  Customer        
2076   58258534  Customer        
2077   58258534  Pro             
2157   58277566  Pro             
2166   58277566  Customer        
2167   58277566  Pro             
2172   58277896  Pro             
2176   58277896  Pro             
2196   58281589  Pro             
2234   58314406  Customer        
2304   58329817  Pro             
2305   58329817  Customer        
2309   58329817  Pro             
2310   58329817  Pro             
2336   58336618  Customer        
2361   58341912  Customer        
2382   58341912  Pro             
2452   58365146  Pro             
2455   58365146  Customer        
2465   58365146  Customer        
2485   58385706  Pro             
2531   58394552  Customer        
2534   58394552  Pro             
2535   58394552  Pro             
2536   58394552  Pro             
2546   58398277  Pro             
2547   58398277  Pro             
2548   58398277  Pro           

### Total 1599 Conversations

- doing preidctions on bid level
- can also do predictions on the chat / pro level. and then aggregate it afterwards. 

In [86]:
df.columns

Index(['bid_id', 'message_timestamp', 'message_sender', 'message', 'category',
       'agent_group', 'is_hired', 'is_location', 'is_contact_info',
       'is_scheduling', 'is_price', 'is_payment'],
      dtype='object')

In [89]:
df[df.is_location == True][['bid_id', 'message_sender', 'message', 'is_location']]

bid_id message_sender  \
0      18314236  Customer        
8      30265067  Pro             
9      30265067  Customer        
11     37749231  Customer        
29     37749231  Customer        
31     37749231  Customer        
36     40733372  Customer        
40     40733372  Customer        
41     42126696  Customer        
44     42126696  Pro             
45     42126696  Customer        
54     42530966  Pro             
60     42597980  Pro             
61     42597980  Customer        
62     42597980  Pro             
77     45816217  Pro             
86     46086074  Pro             
90     46086074  Pro             
92     46086074  Pro             
96     46086074  Pro             
97     46086074  Customer        
107    46267079  Pro             
108    46267079  Pro             
123    47929127  Customer        
124    47929127  Pro             
132    48887274  Customer        
137    52134641  Pro             
149    53324368  Pro             
150    53324368  Customer        
160    53924583  Customer        
161    53924583  Pro             
162    53924583  Customer        
171    54064853  Customer        
174    54226558  Pro             
176    54226558  Pro             
177    54226558  Customer        
179    54226558  Customer        
193    54514926  Customer        
198    54715968  Pro             
199    54715968  Customer        
217    54853421  Pro             
236    55258636  Customer        
241    55258636  Customer        
242    55258636  Pro             
243    55258636  Customer        
245    55258636  Pro             
251    55577457  Pro             
252    55577457  Customer        
263    56048726  Customer        
283    56434850  Customer        
286    56476268  Customer        
295    56523929  Pro             
296    56523929  Customer        
298    56770358  Customer        
299    56770358  Pro             
300    56770358  Customer        
301    56770358  Pro             
310    56897154  Pro             
311    56897154  Customer        
314    56897154  Customer        
321    56897154  Pro             
352    57434360  Pro             
353    57434360  Customer        
354    57434360  Pro             
363    57435440  Pro             
364    57435440  Customer        
381    57496816  Pro             
396    57562369  Pro             
406    57565517  Pro             
423    57602633  Customer        
426    57603564  Customer        
427    57603564  Pro             
428    57603564  Customer        
436    57627161  Pro             
453    57646568  Pro             
458    57648519  Pro             
465    57648519  Customer        
471    57648519  Customer        
475    57666361  Pro             
503    57680430  Pro             
504    57680430  Customer        
505    57680430  Pro             
506    57680430  Customer        
517    57706474  Pro             
526    57713786  Pro             
527    57713786  Customer        
541    57720450  Customer        
555    57722568  Customer        
564    57723640  Pro             
567    57723640  Customer        
568    57723640  Pro             
574    57723640  Pro             
575    57723640  Customer        
610    57725153  Pro             
611    57725153  Customer        
634    57734487  Pro             
635    57734487  Customer        
665    57744433  Pro             
668    57744433  Pro             
669    57744433  Customer        
677    57744433  Customer        
678    57744433  Customer        
683    57745699  Pro             
684    57745699  Customer        
688    57745699  Customer        
701    57746709  Customer        
702    57746709  Pro             
705    57746709  Pro             
707    57746709  Pro             
723    57753052  Customer        
724    57753052  Customer        
725    57753052  Pro             
726    57753052  Customer        
738    57759662  Customer        
739    57759662  Customer        
740    57759662  Pro             
743    57763062  Customer      

In [90]:
bid_level_messages = df.groupby('bid_id')['message'].apply(lambda x: " ".join(x)).reset_index()

### Model

In [96]:
df.head(2)

bid_id               message_timestamp message_sender  \
0  18314236  2018-01-31 23:16:50.788616 UTC  Customer        
1  27365009  2018-02-11 16:54:15.485935 UTC  Customer        

                                                                                                                                                                                                                                                                                                                message  \
0  Hello Brian. You helped us a few years back and we are in need of an electrician again!  Are you able to install a new electrical hook up for a new spa we have purchased?  It requires a dedicated hook up for a 240v spa and will be outdoors. We are in Bay Park area just off I-5. Please let me know... Thanks!   
1  Sounds good! What's next?                                                                                                                                                                                                                                                                                              

                       category agent_group  is_hired  is_location  \
0  Electrical and Wiring Repair  agent_3     False     True          
1  Nutritionist                  agent_2     False     False         

   is_contact_info  is_scheduling  is_price  is_payment  
0  False            False          False     False       
1  False            False          False     False

In [133]:
hired = df.groupby('bid_id')['is_hired'].apply(lambda x: x.any()).reset_index()
location = df.groupby('bid_id')['is_location'].apply(lambda x: x.any()).reset_index()
contact_info = df.groupby('bid_id')['is_contact_info'].apply(lambda x: x.any()).reset_index()
scheduling = df.groupby('bid_id')['is_scheduling'].apply(lambda x: x.any()).reset_index()
price = df.groupby('bid_id')['is_price'].apply(lambda x: x.any()).reset_index()
payment = df.groupby('bid_id')['is_payment'].apply(lambda x: x.any()).reset_index()

In [135]:
bid_level_messages = messages.groupby('bid_id')['message'].apply(lambda x: " ".join(x)).reset_index()
bid_level_messages = pd.merge(bid_level_messages, hired, on="bid_id")
bid_level_messages = pd.merge(bid_level_messages, location, on="bid_id")
bid_level_messages = pd.merge(bid_level_messages, contact_info, on="bid_id")
bid_level_messages = pd.merge(bid_level_messages, scheduling, on="bid_id")
bid_level_messages = pd.merge(bid_level_messages, price, on="bid_id")
bid_level_messages = pd.merge(bid_level_messages, payment, on="bid_id")

In [137]:
bid_level_messages.head()

bid_id  \
0  18314236   
1  27365009   
2  29404730   
3  30265067   
4  31521550   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            message  \
0  Hello Brian. You helped us a few years back and we are in need of an electrician again!  Are you able to install a new electrical hook up for a new spa we have purchased?  It requires a dedicated hook up for a 240v spa and will be outdoors. We are in Bay Park area just off I-5. Please let me know... Thanks!                                                                                                                                                                                                                                                                                               
1  Sounds good! What's next? Hi Cayatana, nice to &quotesee&quote you back! Since it's been two years since we last spoke, perhaps you can tell me if you are still looking for the same thing. How would you like to work together...remotely or in-person? What is your schedule like? Once we determine our first session, you would send payment before hand to my PayPal account before we proceed. I will also send you some forms to complete prior to our session, as well. Best, Amy Hi! I’m currently traveling but will reach out as soon as I get back. Thanks! Sounds good and safe travels! Best, Amy   
2  Greetings..\nAre you available for resume writing?                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 
3  What's your next availability? I would like to get an  estimate for siding repair April. Can likely do est this wk & Work maybe the next. let me know your phone # & address.  Tx. Wade 4 Cameroons Pl. Durham 919-358-2996                                                                                                                                                                                                                                                                                                                                                                                        
4  Can you get the door too if I give you photos and measurement                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      

   is_hired  is_location  is_contact_info  is_scheduling  is_price  is_payment  
0  False     True         False            False          False     False       
1  False     False        False            True           False     True        
2  False     False        False            True           False     False   

In [186]:
terms = ["review", "reviews", "leave us a review", "the review", "rating",
         "hire", "hired", "hiring", "as hired",
         "booking request", "book", 
         "appointment", "contract",
         "reschedule", "schedule", "scheduled",
         "confirming", "confirmed", "confirm", "let's do it",
         "see you", "see u", "see you at", "see you on",
         "on my way", "on our way", "on the way",
         "be there", "is there", "almost there", "get there", 
         "arrive by", "arrive", "eta", 
         "pay", "credit card", "cash", "check", "debit", "invoice", "payment",
         "charges", "charging", "charged",
         "phone number", "contact me", "call me", "number is", "a call", "my cell",
         "my number", "text me", "my phone", "your phone", "can call", "please call",
         "email address", "@gmail.com", "your email", "my email",
         "my address", "are you located", "me the address", 
         "send me your address", "what's your address", "i can meet you",
         "home address", "physical address", "the address", "your address",
         "finished", "finishing", "your work", "my work",
         "available", "full address", "address is"
        ]

### Hired Precision and Recall

In [199]:
def display_info_row_hire(term):
    predicted_hires = bid_level_messages['message'].str.contains(term, case=False)
    predicted_hires = predicted_hires[predicted_hires == True]
    ground_truth = bid_level_messages.loc[predicted_hires.index][['is_hired']] # out of the predicted positives, what's the ground truth
    tp = ground_truth[ground_truth['is_hired'] == True] # ones that are actually hired
    
    precision = tp.shape[0] / predicted_hires.shape[0]
    recall = tp.shape[0] / bid_level_messages[bid_level_messages.is_hired == True].shape[0]
    num_terms = tp.shape[0]
    return [term, 
            "{0:.0f}%".format(precision*100), 
            "{0:.0f}%".format(recall*100), 
            num_terms]

### Location Precision and Recall

In [175]:
def display_info_row_location(term):
    predicted_hires = bid_level_messages['message'].str.contains(term, case=False)
    predicted_hires = predicted_hires[predicted_hires == True]
    ground_truth = bid_level_messages.loc[predicted_hires.index][['is_location']] # out of the predicted positives, what's the ground truth
    tp = ground_truth[ground_truth['is_location'] == True] # ones that are actually hired
    
    precision = tp.shape[0] / predicted_hires.shape[0]
    recall = tp.shape[0] / bid_level_messages[bid_level_messages.is_location == True].shape[0]
    num_terms = tp.shape[0]
    return [term, 
            "{0:.0f}%".format(precision*100), 
            "{0:.0f}%".format(recall*100), 
            num_terms]

### Contact Information Precision and Recall

In [138]:
def display_info_row_contact_info(term):
    predicted_hires = bid_level_messages['message'].str.contains(term, case=False)
    predicted_hires = predicted_hires[predicted_hires == True]
    ground_truth = bid_level_messages.loc[predicted_hires.index][['is_contact_info']] # out of the predicted positives, what's the ground truth
    tp = ground_truth[ground_truth['is_contact_info'] == True] # ones that are actually hired
    
    precision = tp.shape[0] / predicted_hires.shape[0]
    recall = tp.shape[0] / bid_level_messages[bid_level_messages.is_contact_info == True].shape[0]
    num_terms = tp.shape[0]
    return [term, 
            "{0:.0f}%".format(precision*100), 
            "{0:.0f}%".format(recall*100), 
            num_terms]

### Scheduling

In [193]:
def display_info_row_scheduling(term):
    predicted_hires = bid_level_messages['message'].str.contains(term, case=False)
    predicted_hires = predicted_hires[predicted_hires == True]
    ground_truth = bid_level_messages.loc[predicted_hires.index][['is_scheduling']] # out of the predicted positives, what's the ground truth
    tp = ground_truth[ground_truth['is_scheduling'] == True] # ones that are actually hired
    
    precision = tp.shape[0] / predicted_hires.shape[0]
    recall = tp.shape[0] / bid_level_messages[bid_level_messages.is_scheduling == True].shape[0]
    num_terms = tp.shape[0]
    return [term, 
            "{0:.0f}%".format(precision*100), 
            "{0:.0f}%".format(recall*100), 
            num_terms]

In [203]:
key_terms = pd.DataFrame(columns=('Term', 'Precision', 'Recall', 'Count'))
for i, term in enumerate(terms):
    key_terms.loc[i] = display_info_row_scheduling(term)

In [204]:
key_terms

Term Precision Recall Count
0   review                92%       15%    210 
1   reviews               94%       9%     121 
2   leave us a review     100%      0%     2   
3   the review            100%      0%     4   
4   rating                87%       1%     20  
5   hire                  89%       11%    152 
6   hired                 89%       5%     73  
7   hiring                84%       2%     27  
8   as hired              95%       1%     20  
9   booking request       100%      1%     10  
10  book                  93%       17%    233 
11  appointment           99%       11%    155 
12  contract              94%       7%     96  
13  reschedule            100%      5%     65  
14  schedule              100%      28%    387 
15  scheduled             100%      5%     64  
16  confirming            95%       1%     19  
17  confirmed             100%      1%     19  
18  confirm               97%       11%    155 
19  let's do it           100%      0%     4   
20  see you               100%      20%    273 
21  see u                 100%      1%     8   
22  see you at            100%      3%     39  
23  see you on            100%      1%     19  
24  on my way             100%      2%     34  
25  on our way            100%      0%     4   
26  on the way            100%      1%     16  
27  be there              100%      12%    163 
28  is there              94%       7%     99  
29  almost there          100%      0%     1   
30  get there             100%      2%     24  
31  arrive by             100%      0%     2   
32  arrive                96%       5%     65  
33  eta                   89%       12%    166 
34  pay                   88%       13%    179 
35  credit card           97%       3%     35  
36  cash                  95%       6%     76  
37  check                 94%       22%    295 
38  debit                 80%       0%     4   
39  invoice               98%       3%     47  
40  payment               93%       7%     90  
41  charges               73%       1%     8   
42  charging              67%       1%     8   
43  charged               100%      1%     8   
44  phone number          97%       18%    239 
45  contact me            93%       5%     68  
46  call me               95%       15%    207 
47  number is             94%       11%    146 
48  a call                98%       17%    237 
49  my cell               96%       7%     95  
50  my number             95%       7%     90  
51  text me               96%       8%     105 
52  my phone              98%       7%     90  
53  your phone            100%      6%     77  
54  can call              99%       7%     100 
55  please call           93%       6%     82  
56  email address         93%       8%     107 
57  @gmail.com            92%       11%    147 
58  your email            91%       7%     92  
59  my email              91%       5%     73  
60  my address            98%       5%     65  
61  are you located       84%       2%     26  
62  me the address        96%       2%     26  
63  send me your address  100%      3%     37  
64  what's your address   100%      1%     10  
65  i can meet you        100%      1%     19  
66  home address          100%      0%     5   
67  physical address      100%      0%     4   
68  the address           98%       11%    156 
69  your address          100%      11%    148 
70  finished              97%       3%     38  
71  finishing             100%      0%     5   
72  your work             94%       2%     29  
73  my work               96%       7%     98  
74  available             100%      36%    487 
75  full address          100%      0%     5   
76  address is            98%       12%    166

In [205]:
key_terms.sort_values(by=['Precision'], ascending=False)

Term Precision Recall Count
54  can call              99%       7%     100 
11  appointment           99%       11%    155 
76  address is            98%       12%    166 
60  my address            98%       5%     65  
39  invoice               98%       3%     47  
48  a call                98%       17%    237 
52  my phone              98%       7%     90  
68  the address           98%       11%    156 
44  phone number          97%       18%    239 
70  finished              97%       3%     38  
35  credit card           97%       3%     35  
18  confirm               97%       11%    155 
62  me the address        96%       2%     26  
51  text me               96%       8%     105 
32  arrive                96%       5%     65  
73  my work               96%       7%     98  
49  my cell               96%       7%     95  
46  call me               95%       15%    207 
8   as hired              95%       1%     20  
50  my number             95%       7%     90  
16  confirming            95%       1%     19  
36  cash                  95%       6%     76  
72  your work             94%       2%     29  
47  number is             94%       11%    146 
12  contract              94%       7%     96  
28  is there              94%       7%     99  
1   reviews               94%       9%     121 
37  check                 94%       22%    295 
55  please call           93%       6%     82  
56  email address         93%       8%     107 
45  contact me            93%       5%     68  
40  payment               93%       7%     90  
10  book                  93%       17%    233 
57  @gmail.com            92%       11%    147 
0   review                92%       15%    210 
59  my email              91%       5%     73  
58  your email            91%       7%     92  
33  eta                   89%       12%    166 
5   hire                  89%       11%    152 
6   hired                 89%       5%     73  
34  pay                   88%       13%    179 
4   rating                87%       1%     20  
61  are you located       84%       2%     26  
7   hiring                84%       2%     27  
38  debit                 80%       0%     4   
41  charges               73%       1%     8   
42  charging              67%       1%     8   
25  on our way            100%      0%     4   
30  get there             100%      2%     24  
64  what's your address   100%      1%     10  
65  i can meet you        100%      1%     19  
66  home address          100%      0%     5   
67  physical address      100%      0%     4   
69  your address          100%      11%    148 
29  almost there          100%      0%     1   
31  arrive by             100%      0%     2   
71  finishing             100%      0%     5   
3   the review            100%      0%     4   
2   leave us a review     100%      0%     2   
74  available             100%      36%    487 
75  full address          100%      0%     5   
63  send me your address  100%      3%     37  
27  be there              100%      12%    163 
24  on my way             100%      2%     34  
43  charged               100%      1%     8   
9   booking request       100%      1%     10  
26  on the way            100%      1%     16  
14  schedule              100%      28%    387 
15  scheduled             100%      5%     64  
53  your phone            100%      6%     77  
17  confirmed             100%      1%     19  
19  let's do it           100%      0%     4   
20  see you               100%      20%    273 
21  see u                 100%      1%     8   
22  see you at            100%      3%     39  
23  see you on            100%      1%     19  
13  reschedule            100%      5%     65

In [ ]:
# the number of people that are hired...
bid_level_messages[bid_level_messages.hired == True].shape[0]

Improvements:
- combination of words, more complex regex rules
    - multiple words to be present
    - eliminate certain words
    - use other metadata for prediction
- analyze the false positives -- predicted as hires but are actually not
    - sometimes people cancel
    - sometimes they use the word but not in context of hiring
    - sometimes I think it should be marked as hired because they seemed to meet
    - can do more research

### Analyzing Specific Words

- using terms from # https://docs.google.com/spreadsheets/d/1736DS7PE-zBbmLBEr00Z3LVBVCJhi-mB6QJADa--xdA/edit#gid=0

### Hired

In [142]:
# term = r'^(?=.*be there)(?=.*review)(?=.*[^reviewed])'
# term = r'^(?=.*hired)(?=.*review )((?!reviewed))*$'
term = r'^(?=.*be there)(?=.*review)(?!.*reviewed)'
predicted_hires = bid_level_messages['message'].str.contains(term, case=False)
predicted_hires = predicted_hires[predicted_hires == True]
ground_truth = bid_level_messages.loc[predicted_hires.index][['is_hired']] # out of the predicted positives, what's the ground truth
tp = ground_truth[ground_truth['is_hired'] == True] # ones that are actually hired

precision = tp.shape[0] / predicted_hires.shape[0]
recall = tp.shape[0] / bid_level_messages[bid_level_messages.is_hired == True].shape[0]
num_terms = tp.shape[0]
print("Term:", term, 
      "\nPrecision:", "{0:.0f}%".format(precision*100),
      "\nRecall:", "{0:.0f}%".format(recall*100),
      "\nCount:", num_terms)

Term: ^(?=.*be there)(?=.*review)(?!.*reviewed) 
Precision: 100% 
Recall: 2% 
Count: 7


### Location

In [170]:
# term = r'^(?=.*be there)(?=.*review)(?=.*[^reviewed])'
# term = r'^(?=.*hired)(?=.*review )((?!reviewed))*$'
# need to debug and figure out why the count is different...
# spend some time to make sure that the regex is correct and doesn't underrepresent anything

# term = r'^(?=.*home address)' # r'^.*home address.*$'
term = "on my way"
predicted_hires = bid_level_messages['message'].str.contains(term, case=False, regex=True)
predicted_hires = predicted_hires[predicted_hires == True]
ground_truth = bid_level_messages.loc[predicted_hires.index][['is_location']] # out of the predicted positives, what's the ground truth
tp = ground_truth[ground_truth['is_location'] == True] # ones that are actually hired

precision = tp.shape[0] / predicted_hires.shape[0]
recall = tp.shape[0] / bid_level_messages[bid_level_messages.is_location == True].shape[0]
num_terms = tp.shape[0]
print("Term:", term, 
      "\nPrecision:", "{0:.0f}%".format(precision*100),
      "\nRecall:", "{0:.0f}%".format(recall*100),
      "\nCount:", num_terms)

Term: on my way 
Precision: 94% 
Recall: 3% 
Count: 32


In [171]:
ground_truth

is_location
5     True       
14    True       
101   True       
125   True       
216   True       
264   True       
294   True       
313   True       
487   True       
513   True       
547   True       
588   True       
595   True       
657   True       
667   True       
740   True       
753   True       
759   True       
818   True       
873   True       
996   True       
1029  True       
1046  False      
1071  True       
1112  True       
1135  True       
1144  True       
1158  True       
1217  True       
1415  False      
1456  True       
1508  True       
1553  True       
1591  True

In [173]:
bid_level_messages.loc[1415]

bid_id             62671285                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               
message            Will call in be am to set up a time. Ok Hi Marc just wanted to check up on you to see when you will be calling to set a time Call within the hour. Driving and no reception here. Ok can't wait to hear fr

In [ ]:
df[df.bid_id == 63182593]

### Metadata of hiring messages:
- message sender, pro vs customer distribution
- category
- quick reply vs not quick reply (are there quick replies that we can just automatically classify as hire?)